# Run Simulator

This example demonstrates how to execute a simulator (in serial or parallel) at a set of samples.

### Import

First, we need to import the class `RunSimulator` from the module `psimpy.simulator.run_simulator`.

In [1]:
from psimpy.simulator.run_simulator import RunSimulator

### Instantiation

Then we need to create a new class that inherets from the class `RunSimulator` and override the abstract method `simulator()`. The `simulator()` method cannot have any positional-only arguments, has to contain the `**kwargs` argument and it has to return the results in form of a numpy array.

Here we're going to use the method `run` of the class `MPM` from the module `psimpy.simulator.mass_point_model` as our simulator. This method solves the mass point model using the ode solver `scipy.integrate.ode` given following inputs: topography, friction parameters, and initial condition of the mass point (location and velocity).

To do this, we first define the child class `MpmSolver`, override the `__init__` method to create a new instance of `MPM`, then we override the `simulator()` method in order to return the outputs of the method `run()` from the `MPM` class. 

In [2]:
from psimpy.simulator.mass_point_model import MPM

class MpmSolver(RunSimulator):
    def __init__(self, *args, **kwargs):
        self.mpm = MPM()
        super(MpmSolver, self).__init__(*args, **kwargs)
        
    def simulator(self, elevation, coulomb_friction, turbulent_friction, x0, y0,
            ux0=0, uy0=0, dt=1, tend=300, t0=0, g=9.8, atol=1e-4, rtol=1e-4,
            curvature=False, **kwargs):
        
        return self.mpm.run(elevation=elevation, coulomb_friction=coulomb_friction,
                            turbulent_friction=turbulent_friction, x0=x0, y0=y0, ux0=ux0,
                            uy0=uy0, dt=dt, tend=tend, t0=t0, g=g, atol=atol, rtol=rtol,
                            curvature=curvature)

Now we can create a new instance of `MpmSolver`. In order to initialize `MpmSolver`, which has the same `__init__()` method as `RunSimulator`, the user needs to define the parent folder to save simulation outputs `sim_dir`, a list consists of all variable input names `var_inp_name` and a dictionary consists of all fixed input name-value pairs `fix_inp`.

In [3]:
import os

sim_dir = os.path.join(os.path.abspath(''), "../../tests/sim_log")
fix_inp = {
    "elevation" :  os.path.join(os.path.abspath(''), "../../tests/data/mpm_topo.asc"), 
    "x0" : 800,
    "y0" : 2000,
    "ux0" : 1e-10,
    "uy0" : 1e-10,
    "dt" : 2,
    "tend" : 600
}
var_inp_name=["coulomb_friction", "turbulent_friction"]

mpmsolver = MpmSolver(sim_dir=sim_dir, var_inp_name=var_inp_name, fix_inp=fix_inp)

`coulomb_friction` and `turbulent_friction` are variable inputs and the other inputs are fixed. We may vary `coulomb_friction` between 0.1 to 0.3 and `turbulent_friction` between 500 to 2000.

In [4]:
import numpy as np
import itertools

cf = np.arange(0.1, 0.3, 0.05)
tf = np.arange(500, 2000, 150)

var_samples = np.array([x for x in itertools.product(cf, tf)])

## Serial Execution
In order to perform a serial execution of the simulator, we need to pass `var_samples` to the `serial_run()` method. The user can also specify optional arguments like `prefixes`, `append` or `save_out`. Here we like to save the results with the "serial" prefixes.

In [5]:
serial_prefixes = ["serial"+str(i) for i in range(len(var_samples))]

mpmsolver.serial_run(var_samples=var_samples, prefixes=serial_prefixes, save_out=True)

To check the results one could either check `mpmsolver.outputs` or load the files available in `sim_dir`.

## Parallel Execution
Now let's run the same simulator in parallel. Once again we prepare samples of the variable inputs.

In [6]:
cf = np.arange(0.1, 0.30, 0.04)
tf = np.arange(500, 2000, 100)

var_samples = np.array([x for x in itertools.product(cf, tf)])

This time we will pass the first 40 samples and then append the rest. We can also specify the maximum number of tasks running in parallel `max_workers` as well as `prefixes`, `append` and `save_out`.

In [7]:
mpmsolver.parallel_run(var_samples=var_samples[:40], max_workers=2)

Now, let's append the rest of the samples.

In [8]:
mpmsolver.parallel_run(var_samples=var_samples[40:], append=True, max_workers=2)

Same as serial execution, we can check the results either by using `mpmsolver.outputs` or loading the files available in `sim_dir`.